In [1]:
from PIL import Image
import numpy as np
import json
with open("/raid/data_modal/IAPR_TC-12/img_tagslabel.json","r") as f:
    taglabel = json.load(f)
with open('/raid/data_modal/IAPR_TC-12/filterd_label_name.json', 'r') as f:
    filterd_label_name  = json.load(f)
with open('/raid/data_modal/IAPR_TC-12/class_name.json', 'r') as f:
    class_name  = json.load(f)
def display_aipr(image_id):
    dir_path = "/raid/data_modal/IAPR_TC-12/hashing_images/"
    this_name = np.array(class_name)[np.array(taglabel[str(image_id)]["label"])>0]
    print(this_name)
    print(taglabel[str(image_id)]["tags"])
    display(Image.open(dir_path+"{}.jpg".format(image_id)))
def get_tag(image_id):
    return taglabel[image_id]["tags"]
def get_label(image_id):
    return np.array(class_name)[np.array(taglabel[str(image_id)]["label"])>0]
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
from logging import log
import re
import numpy as np
import os.path as op
from hashing_module.triplet_loss import *
from torch.autograd.grad_mode import F

from torch.nn.modules import loss
from torch.utils.data.sampler import Sampler

import argparse
from oscar.modeling.modeling_bert import HashingformerALL,HashingformerSingle,normal_label
from pytorch_transformers import BertTokenizer, BertConfig
import torch
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler
from tqdm import tqdm
from torch.autograd import Variable
from oscar.utils.tsv_file import TSVFile
from torch.nn import CrossEntropyLoss
import json
import base64
import random
from pytorch_transformers import AdamW, WarmupLinearSchedule, WarmupConstantSchedule
from hashing_module.utils import calc_map_k
from oscar.utils.logger import setup_logger
from oscar.utils.misc import mkdir
class RetrievalDataset(Dataset):
    """ Image/Text Retrieval Dataset"""
    def __init__(self, args,tokenizer,split="train"):
        """
        tokenizer: tokenizer to process caption text.
        args: configureation parameters including max_seq_length, etc.
        split: used to infer the data used for training or testing. 
             All files are in .pt format of a dictionary with image keys and 
             image features (pytorch tensors), captions (list of str, support multiple
             captions per image), labels (list of dictionary or str of all labels),

        """
        super(RetrievalDataset, self).__init__()
        with open(args.tagslabel ,"r") as f:
            self.tagslabel = json.load(f)   
        self.args = args  
        self.split = split      
        self.img_file = args.img_feat_file
        self.img_tsv = TSVFile(self.img_file)
        self.img_keys = list(self.tagslabel.keys())  # img_id as int
        imgid2idx_file = op.join(op.dirname(self.img_file), 'imageid2idx.json')
        self.image_id2idx = json.load(open(imgid2idx_file))  # img_id as string
        with open(args.class_name,"r") as f:
            self.class_name = json.load(f)
            self.class_name = np.array(self.class_name)
        if(args.split_keys):
            with open(args.split_keys,"r") as f:
                self.img_keys = json.load(f)
                self.img_keys = [str(i) for i in self.img_keys]
        else:
            random.seed(279834)
            random.shuffle(self.img_keys)
        if(split=="train"):
            self.img_keys = self.img_keys[args.query_size:args.training_size + args.query_size]
            total_label = []
            for i in self.img_keys:
                total_label.append(self.tagslabel[i]["label"])
            self.total_label = torch.Tensor(total_label)
        elif(split=="query"):
            self.img_keys = self.img_keys[:args.query_size]
        else:
            self.img_keys = self.img_keys[args.query_size:args.database_size+ args.query_size]
        label_data_dir = op.dirname(self.img_file)
        label_file = os.path.join(label_data_dir, "label.tsv")
        self.label_tsv = TSVFile(label_file)
        self.labels = {}

        
        for line_no in tqdm(range(self.label_tsv.num_rows())):
            row = self.label_tsv.seek(line_no)
            image_id = row[0]
            if image_id in self.img_keys:
                results = json.loads(row[1])
                objects = results['objects'] if type(
                    results) == dict else results
                self.labels[image_id] = {
                    "image_h": results["image_h"] if type(
                        results) == dict else 600,
                    "image_w": results["image_w"] if type(
                        results) == dict else 800,
                    "class": [cur_d['class'] for cur_d in objects],
                    "boxes": np.array([cur_d['rect'] for cur_d in objects],
                                        dtype=np.float32)
                }
        self.label_tsv._fp.close()
        self.label_tsv._fp = None   
        self.output_mode = 'classification'
        self.tokenizer = tokenizer
        self.max_seq_length = 35
        self.max_img_seq_len = 70
        self.args.max_label_length = args.max_label_length
    def get_od_labels(self, img_key):

        if type(self.labels[img_key]) == str:
            od_labels = self.labels[img_key]
        else:
            od_labels = ' '.join(self.labels[img_key]['class'])
        return od_labels
    def class_tokenize(self,labels,max_length=15):
        all_size = labels.shape[0]
        final_label = []
        for i in range(all_size):
            this_label = torch.zeros((max_length+2))
            class_name = self.class_name[labels[i]>0]
            
            tokens = self.tokenizer.tokenize("".join(class_name))
            tokens = [self.tokenizer.cls_token] + tokens[0:max_length] + [self.tokenizer.sep_token]
            input_ids = self.tokenizer.convert_tokens_to_ids(tokens)
            
            this_label[0:len(input_ids)] = torch.Tensor(input_ids)
            final_label.append(this_label)
        final_label = torch.stack(final_label).long()  
        return final_label  

   
    def tensorize_example(self, text_a, img_feat, text_b=None, 
            cls_token_segment_id=0, pad_token_segment_id=0,
            sequence_a_segment_id=0, sequence_b_segment_id=1):
        tokens_a = self.tokenizer.tokenize(text_a)
        if len(tokens_a) > self.max_seq_length - 2:
            tokens_a = tokens_a[:(self.max_seq_length - 2)]

        tokens = [self.tokenizer.cls_token] + tokens_a + [self.tokenizer.sep_token]
        segment_ids = [cls_token_segment_id] + [sequence_a_segment_id] * (len(tokens_a) + 1)
    
        if text_b:
            tokens_b = self.tokenizer.tokenize(text_b)
            if len(tokens_b) > self.max_seq_length   - 2:#a
                tokens_b = tokens_b[: (self.max_seq_length  - 2)]
            tokens_b = [self.tokenizer.cls_token] +tokens_b+ [self.tokenizer.sep_token]
            segment_ids_b = [sequence_b_segment_id] + [sequence_b_segment_id] * (len(tokens_b) -1)
        #这儿分a padding
        seq_len_a = len(tokens)
        seq_padding_len_a = self.max_seq_length - seq_len_a
        tokens += [self.tokenizer.pad_token] * seq_padding_len_a
        segment_ids += [pad_token_segment_id] * seq_padding_len_a
        input_ids = self.tokenizer.convert_tokens_to_ids(tokens)
        #b padding
        seq_len_b = len(tokens_b)
        seq_padding_len_b = self.max_seq_length - seq_len_b
        tokens_b += [self.tokenizer.pad_token] * seq_padding_len_b
        segment_ids_b += [pad_token_segment_id] * seq_padding_len_b
        input_ids_b = self.tokenizer.convert_tokens_to_ids(tokens_b)
        #合并
        tokens_show = tokens+tokens_b
        input_ids = input_ids+input_ids_b
        segment_ids = segment_ids+segment_ids_b
        # image features
        img_len = img_feat.shape[0]

        if img_len > self.max_img_seq_len:
            img_feat = img_feat[0 : self.max_img_seq_len, :]
            img_len = img_feat.shape[0]
            img_padding_len = 0
        else:
            img_padding_len = self.max_img_seq_len - img_len
            padding_matrix = torch.zeros((img_padding_len, img_feat.shape[1]))
            
            img_feat = torch.cat((img_feat, padding_matrix), 0)

        # generate attention_mask
        att_mask_type = "CLR"
        if att_mask_type == "CLR":
            attention_mask = [1] * seq_len_a + [0] * seq_padding_len_a +[1] * seq_len_b + [0] * seq_padding_len_b +  [1] * img_len + [0] * img_padding_len 


        input_ids = torch.tensor(input_ids, dtype=torch.long)
        attention_mask = torch.tensor(attention_mask, dtype=torch.long)
        segment_ids = torch.tensor(segment_ids, dtype=torch.long)
        return (input_ids, attention_mask, segment_ids, img_feat),tokens_show

    def __getitem__(self, index):
        
        img_key = self.img_keys[index]
      
        feature = self.get_image(img_key)
        tag_list = self.tagslabel[img_key]["tags"]
        if(isinstance(tag_list,list)):
            caption = ""
            for i in tag_list:
                caption+=i+" "
            caption=caption.strip()
        else:#is a string
            caption  = tag_list
        od_labels = self.get_od_labels(img_key)
        example,tokens_show = self.tensorize_example(caption, feature, text_b=od_labels)
        label = self.tagslabel[img_key]["label"]
        label=torch.tensor(label, dtype=torch.long)
        if(self.split=="train"):
            raw_label = self.generate_samples(label,self.args.negative_number)
            #negative_label = normal_label(raw_label,max_length = self.args.max_label_length )
            negative_label = self.class_tokenize(raw_label,max_length = self.args.max_label_length )
            return tuple(list(example) + [label,negative_label,raw_label]),img_key
        else:
            return tuple(list(example) +[tokens_show]+[label]),img_key

    def generate_samples(self, label,negative_number = 99):
        mask = 1-label #
        negative_samples = []
        positive_sample = label 
        all_index =torch.arange(self.total_label.shape[0])
        while(len(negative_samples)<negative_number//2):
            smaples=  torch.from_numpy(np.random.choice(2, self.args.class_number,p=[1-5/self.args.class_number,5/self.args.class_number]))
            is_positive = (smaples*label).sum()>0
            if(not is_positive):
                negative_samples.append(smaples)
        
        while(len(negative_samples)<negative_number):
            sim = torch.matmul(label.unsqueeze(0).float(),self.total_label.float().t()).squeeze(0)>0
            negative = all_index[~sim]
            smaples_index=  np.random.choice(negative.numpy(), 1)[0]
            negative_samples.append(self.total_label[smaples_index])        
        final_sample = [positive_sample]+negative_samples
        final_sample = torch.stack(final_sample)
        return final_sample
    def get_image(self, image_id):
        image_idx = self.image_id2idx[str(image_id)]
        row = self.img_tsv.seek(image_idx)
        num_boxes = int(row[1])
        features = np.frombuffer(base64.b64decode(row[-1]),
                                 dtype=np.float32).reshape((num_boxes, -1)).copy()
        t_features = torch.from_numpy(features)
        return t_features

    def __len__(self):
        return len(self.img_keys) 

In [2]:
class Opt():
    def __init__(self) -> None:
        self.use_gpu = True
        self.training_size = 10000
        self.query_size = 2000
        self.bit = 64
        self.database_size = 18000 
        self.gamma = 1
        self.eta = 1
        self.valid = True
        self.batch_size = 64
        self.margin = 0.4
        self.gamma = 1
        self.beta = 1
        self.alpha = 1
opt = Opt()

In [3]:
parser = argparse.ArgumentParser()
parser.add_argument("--num_train_epochs", default=1000, type=int, 
                    help="Total number of training epochs to perform.")
parser.add_argument("--class_name", default='/raid/data_modal/MIR_Flickr_25k/class_name.json"', type=str, required=False,
                    help="The input data dir with all required files.")
parser.add_argument("--split_keys", default='', type=str, required=False,
                    help="split_keys")
parser.add_argument("--tagslabel", default='MIR_Flickr_25k/img_tagslabel.json', type=str, required=False,
                    help="The input data dir with all required files.")
parser.add_argument("--img_feat_file", default='/MIR_Flickr_25k/vinvl_data/vinvl_vg_x152c4/predictions.tsv', type=str, required=False,
                    help="The absolute address of the image feature file.")
parser.add_argument("--output_dir", default='output/log_aipr', type=str, required=False,
                    help="The output directory to save checkpoint and test results.")
parser.add_argument("--num_workers", default=4, type=int, help="Workers in dataloader.")
parser.add_argument("--eval_model_dir", type=str, default='', 
                    help="Model directory for evaluation.")   
parser.add_argument("--do_lower_case", action='store_true', 
                    help="Set this flag if you are using an uncased model.")   
parser.add_argument("--output_file", type=str, default='', 
                    help="Model directory for evaluation.")  
parser.add_argument("--learning_rate", default=2e-5, type=float, help="The initial lr.")
parser.add_argument("--weight_decay", default=0.05, type=float, help="Weight deay.")
parser.add_argument("--adam_epsilon", default=1e-8, type=float, help="Epsilon for Adam.")
parser.add_argument("--max_grad_norm", default=1.0, type=float, help="Max gradient norm.")
parser.add_argument("--warmup_steps", default=0, type=int, help="Linear warmup.")
parser.add_argument("--scheduler", default='linear', type=str, help="constant or linear.")
parser.add_argument("--bit", default=64, type=int, help="constant or linear.")
parser.add_argument("--class_number", default=255, type=int, help="constant or linear.")  
parser.add_argument("--training_size", default=10000, type=int, help="constant or linear.") 
parser.add_argument("--query_size", default=2000, type=int, help="constant or linear.") 
parser.add_argument("--database_size", default=18000, type=int, help="constant or linear.")
parser.add_argument("--no_pretrain", action='store_true', help="constant or linear.")
parser.add_argument("--negative_number", default=9, type=int, help="constant or linear.")
parser.add_argument("--max_label_length", default=10, type=int, help="constant or linear.")
lists = [
                "--tagslabel",
                "/raid/data_modal/IAPR_TC-12/img_tagslabel.json",
                "--img_feat_file",
                "/raid/data_modal/IAPR_TC-12/vinvl/use_for_vinvl/feature.tsv",
                "--do_lower_case",
                "--eval_model_dir",
                "/raid/whf/ObjectContrastiveTransformer/output/IAPR_label_analysis/checkpoint-348",
                "--training_size","10000",
                "--query_size","100",
                "--database_size","18000",
                "--class_number","255",
                "--class_name","/raid/data_modal/IAPR_TC-12/class_name.json",
            ]

# lists =  [
#                 "--tagslabel",
#                 "/raid/data_modal/MIR_Flickr_25k/new_img_tagslabel.json",
#                 "--img_feat_file",
#                 "/raid/data_modal/MIR_Flickr_25k/vinvl_data/use_for_vinvl/feature.tsv",
#                 "--do_lower_case",
#                 "--output_dir",
#                 "output/unit_pretrain_flicker",
#                 "--eval_model_dir",
#                 "/raid/whf/ObjectContrastiveTransformer/output/case_study_flicker/checkpoint-22",
#                 "--training_size","10000",
#                 "--query_size","2000",
#                 "--database_size","18015",
#                 "--class_number","24",
#                 "--class_name","/raid/data_modal/MIR_Flickr_25k/class_name.json",
               
#             ]
args = parser.parse_args(lists)

In [4]:
opt.class_number = args.class_number
device = torch.device("cuda")
config_class, tokenizer_class = BertConfig, BertTokenizer
checkpoint = args.eval_model_dir
tokenizer = tokenizer_class.from_pretrained(checkpoint, do_lower_case=args.do_lower_case)
config = config_class.from_pretrained(checkpoint)
config.output_attentions = True
config.class_number = opt.class_number
config.bit = args.bit
model = HashingformerALL(None,config)
if(not args.no_pretrain):
    if(not os.path.exists(checkpoint+"/pytorch_model.bin")):
        sd = torch.load(checkpoint+"/model.cpkt", map_location="cpu")
    else:
        sd = torch.load(checkpoint+"/pytorch_model.bin", map_location="cpu")
    missing, unexpected = model.load_state_dict(sd, strict=False)  
model.to(device)
model_base = HashingformerSingle(None,config)
sd = torch.load("/raid/whf/ObjectContrastiveTransformer/output/case_study_IAPR_single/checkpoint-265"+"/model.cpkt", map_location="cpu")
missing, unexpected = model_base.load_state_dict(sd, strict=False) 
model_base.to(device)

HashingformerSingle(
  (bert): BertImgModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): FusedLayerNorm(torch.Size([768]), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): CaptionBertEncoder(
      (layer): ModuleList(
        (0): CaptionBertLayer(
          (attention): CaptionBertAttention(
            (self): CaptionBertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm):

In [5]:
query_dataset = RetrievalDataset(args,tokenizer,"query")
retrieval_dataset = RetrievalDataset(args,tokenizer,"retrieval")

100%|██████████| 17585/17585 [00:07<00:00, 2221.82it/s]


In [6]:
def generate_code(model, query_dataloader):
    attention_is = []
    attention_ts = []
    keys = []
    token_alls=[]
    for batch,key in tqdm(query_dataloader):
        input_ids = batch[0].long().cuda()
        attention_mask = batch[1].long().cuda()
        token_type_ids = batch[2].long().cuda()
        img_feats = batch[3].cuda()
        token_all = batch[4]
        token_all = np.array(token_all).T.tolist()

        label = batch[5].cuda()
        text_len = input_ids.shape[1]//2
        with torch.no_grad():

            outputs_t = model.bert(input_ids[:,:text_len], position_ids=None, token_type_ids=token_type_ids[:,:text_len],
                                attention_mask=attention_mask[:,:text_len], head_mask=None, img_feats=None) 
        
            outputs_i = model.bert(input_ids[:,text_len:], position_ids=None, token_type_ids=token_type_ids[:,text_len:],
                            attention_mask=attention_mask[:,text_len:], head_mask=None, img_feats=img_feats) 

        attention_is.append(outputs_i[-1])
        attention_ts.append(outputs_t[-1])
        keys.extend(key)
        token_alls.extend(token_all)

    return keys,attention_is,attention_ts,token_alls

def generate_code_single(model, query_dataloader):
    attention_is = []
    attention_ts = []
    keys = []
    token_alls=[]
    for batch,key in tqdm(query_dataloader):
        input_ids = batch[0].long().cuda()
        attention_mask = batch[1].long().cuda()
        token_type_ids = batch[2].long().cuda()
        img_feats = batch[3].cuda()
        token_all = batch[4]
        token_all = np.array(token_all).T.tolist()

        label = batch[5].cuda()
        text_len = input_ids.shape[1]//2
        with torch.no_grad():

            outputs_t = model.bert1(input_ids[:,:text_len], position_ids=None, token_type_ids=token_type_ids[:,:text_len],
                                attention_mask=attention_mask[:,:text_len], head_mask=None, img_feats=None) 
        
            outputs_i = model.bert(input_ids[:,text_len:], position_ids=None, token_type_ids=token_type_ids[:,text_len:],
                            attention_mask=attention_mask[:,text_len:], head_mask=None, img_feats=img_feats) 

        attention_is.append(outputs_i[-1])
        attention_ts.append(outputs_t[-1])
        keys.extend(key)
        token_alls.extend(token_all)

    return keys,attention_is,attention_ts,token_alls

In [7]:
model.eval()
query_sampler = SequentialSampler(query_dataset)
query_dataloader = DataLoader(query_dataset, sampler=query_sampler,
        batch_size=512, num_workers=4)
retrieval_sampler = SequentialSampler(retrieval_dataset)
retrieval_dataloader = DataLoader(retrieval_dataset, sampler=retrieval_sampler,
        batch_size=512, num_workers=4)
keys,attention_is,attention_ts,token_alls = generate_code(model,query_dataloader)
keys_base,attention_is_base,attention_ts_base,token_alls_base = generate_code_single(model_base,query_dataloader)

100%|██████████| 1/1 [00:01<00:00,  1.52s/it]


In [8]:
print(len(token_alls))

100


In [9]:
attention_is=attention_is[0]
attention_ts=attention_ts[0]
attention_is_base=attention_is_base[0]
attention_ts_base=attention_ts_base[0]

## analysis attention map

In [10]:
def geti(attentions,i):
    final = tuple([a[0:1,0:1,:,:] for a in attentions])
    return final

In [11]:
from bertviz import head_view

In [12]:
attention = geti(attention_ts,0)


In [13]:
head_view(attention, token_alls[0][0:35])

<IPython.core.display.Javascript object>

In [14]:
attention_i = geti(attention_is,0)

In [15]:
head_view(attention_i, token_alls[0][35:]+[str(i) for i in range(70)])

<IPython.core.display.Javascript object>

In [20]:
attention_t_base = geti(attention_ts_base,0)
head_view(attention_t_base, token_alls_base[0][0:35])

<IPython.core.display.Javascript object>

In [18]:
attention_i_base = geti(attention_is_base,0)
head_view(attention_i_base, token_alls_base[0][35:]+[str(i) for i in range(70)])

<IPython.core.display.Javascript object>

In [15]:
len(attention_ts)

12

In [16]:
attention_ts[0].shape

torch.Size([100, 12, 35, 35])

In [22]:
len(attention)
print(attention[0].shape)

torch.Size([1, 1, 35, 35])
